In [1]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

# Imports
import numpy as np
import tensorflow as tf

In [ ]:
# constants
CLASS = 200
SAMPLES_PER_CLASS = 500
TOTAL_SAMPLES = CLASS * SAMPLES_PER_CLASS
COLOR_CHANNELS = 3
IMAGE_WIDTH = 64
IMAGE_HEIGHT = 64
VAL_SAMPLES = 10000

In [2]:
def cnn_model_fn(features, labels, mode):
    """Model function for CNN."""
    # Input Layer
    input_layer = tf.reshape(features["x"], [-1, 64, 64, 3])

    # Convolutional Layer #1
    conv1 = tf.layers.conv2d(inputs=input_layer, filters=32, kernel_size=[5, 5], padding="same", activation=tf.nn.relu)

    # Pooling Layer #1
    pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

    # Convolutional Layer #2 and Pooling Layer #2
    conv2 = tf.layers.conv2d(inputs=pool1, filters=64, kernel_size=[5, 5], padding="same", activation=tf.nn.relu)
    pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

    # Dense Layer
    pool2_flat = tf.reshape(pool2, [-1, 16 * 16 * 64])
    dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
    dropout = tf.layers.dropout(inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

    # Logits Layer
    logits = tf.layers.dense(inputs=dropout, units=10)

    predictions = {
        # Generate predictions (for PREDICT and EVAL mode)
        "classes": tf.argmax(input=logits, axis=1),
        # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
        # `logging_hook`.
        "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }

    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

    # Calculate Loss (for both TRAIN and EVAL modes)
    onehot_labels = tf.one_hot(indices=tf.cast(labels, tf.int32), depth=10)
    loss = tf.losses.softmax_cross_entropy(onehot_labels=onehot_labels, logits=logits)

    # Configure the Training Op (for TRAIN mode)
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(loss=loss, global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

    # Add evaluation metrics (for EVAL mode)
    eval_metric_ops = {"accuracy": tf.metrics.accuracy(labels=labels, predictions=predictions["classes"])}
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

In [ ]:
def load_zipped_pickle(filename):
    with gzip.open(filename, 'rb') as f:
        loaded_object = cPickle.load(f)
        return loaded_object

In [3]:
tf.logging.set_verbosity(tf.logging.INFO)

# Our application logic will be added here
def main(unused_argv):
    
    # load data
    print("loading data from file...")
    data = load_zipped_pickle("tinyImageData")
    train_data = np.array(data["train"]["data"], dtype = np.float16)
    train_labels = np.array(data["train"]["target"], dtype = np.float16)
    val_data = np.array(data["val"]["data"], dtype = np.float16)
    val_labels = np.array(data["val"]["target"], dtype = np.float16)

    # Create the Estimator
    tiny_imagenet_clf = tf.estimator.Estimator(model_fn=cnn_model_fn, model_dir="tiny_imagenet_cnn_model")

    # Set up logging for predictions
    # Log the values in the "Softmax" tensor with label "probabilities"
    tensors_to_log = {"probabilities": "softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook(tensors=tensors_to_log, every_n_iter=500)

    # Train the model
    train_input_fn = tf.estimator.inputs.numpy_input_fn(x={"x": train_data}, y=train_labels, batch_size=100,
                                                        num_epochs=None, shuffle=True)
    tiny_imagenet_clf.train(input_fn=train_input_fn, steps=20000, hooks=[logging_hook])

    # Evaluate the model and print results
    eval_input_fn = tf.estimator.inputs.numpy_input_fn(x={"x": val_data}, y=val_labels, num_epochs=1, shuffle=False)
    eval_results = tiny_imagenet_clf.evaluate(input_fn=eval_input_fn)
    print(eval_results)

if __name__ == "__main__":
    tf.app.run()

Successfully downloaded train-images-idx3-ubyte.gz 9912422 bytes.
Extracting MNIST-data/train-images-idx3-ubyte.gz
Successfully downloaded train-labels-idx1-ubyte.gz 28881 bytes.
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Successfully downloaded t10k-images-idx3-ubyte.gz 1648877 bytes.
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Successfully downloaded t10k-labels-idx1-ubyte.gz 4542 bytes.
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_task_type': 'worker', '_is_chief': True, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f8c58f5fbd0>, '_save_checkpoints_steps': None, '_keep_checkpoint_every_n_hours': 10000, '_service': None, '_num_ps_replicas': 0, '_tf_random_seed': 1, '_master': '', '_num_worker_replicas': 1, '_task_id': 0, '_log_step_count_steps': 100, '_model_dir': '/tmp/mnist_convnet_m

INFO:tensorflow:loss = 2.29883, step = 1
INFO:tensorflow:probabilities = [[ 0.12066089  0.09177192  0.08230697  0.09834262  0.10862121  0.08557712
   0.09963576  0.11174634  0.08807424  0.113263  ]
 [ 0.11638752  0.10154912  0.08345377  0.09840482  0.10576021  0.10596216
   0.09906538  0.09579507  0.09204745  0.10157452]
 [ 0.11218522  0.09880973  0.08457419  0.08278371  0.11583129  0.10165661
   0.09936238  0.09509611  0.08923439  0.12046631]
 [ 0.10418569  0.09703402  0.09237828  0.09547674  0.10162409  0.10714997
   0.09088181  0.10884201  0.08824175  0.11418568]
 [ 0.09685967  0.10833344  0.08531693  0.09565354  0.10476758  0.10188396
   0.09173327  0.09778818  0.10847191  0.1091915 ]
 [ 0.11115864  0.09408502  0.10143555  0.10110552  0.11009073  0.10141836
   0.0978905   0.09802728  0.08409554  0.10069282]
 [ 0.1162221   0.09132236  0.09218914  0.09600237  0.09197277  0.1050546
   0.09931841  0.11506733  0.07986696  0.11298407]
 [ 0.11463751  0.1124474   0.08548289  0.09942668  0.

INFO:tensorflow:global_step/sec: 132.4
INFO:tensorflow:probabilities = [[ 0.10746284  0.10185905  0.0798334   0.10652268  0.10693729  0.10385348
   0.09311959  0.09218854  0.0903194   0.11790369]
 [ 0.12955151  0.10729136  0.077144    0.10552247  0.12493761  0.09491687
   0.09145565  0.09227362  0.07442595  0.10248099]
 [ 0.10914595  0.09443072  0.08817106  0.10049061  0.11515746  0.09437083
   0.09654801  0.09645495  0.09600569  0.10922474]
 [ 0.10809938  0.09464483  0.09589779  0.10286324  0.10474519  0.09326646
   0.10280448  0.09651975  0.09147766  0.10968116]
 [ 0.10727286  0.11241747  0.09599421  0.10040464  0.10437237  0.09572053
   0.09353394  0.10184231  0.09315825  0.0952834 ]
 [ 0.11402233  0.09462992  0.0876559   0.09876563  0.11023424  0.09158742
   0.10143556  0.10113552  0.09192006  0.10861345]
 [ 0.11733966  0.09607358  0.08037316  0.09288958  0.1090375   0.08493345
   0.1133784   0.10062224  0.08788667  0.11746578]
 [ 0.12127262  0.09238914  0.09296466  0.1073747   0.1

INFO:tensorflow:loss = 2.29233, step = 101 (0.750 sec)
INFO:tensorflow:probabilities = [[ 0.11568019  0.1129992   0.08800904  0.10486719  0.09501474  0.10090275
   0.08655346  0.0972936   0.09011657  0.10856327]
 [ 0.09787074  0.09521373  0.08624287  0.1020566   0.12244722  0.09519456
   0.09370591  0.10263035  0.08547134  0.11916664]
 [ 0.12254988  0.09168705  0.08641902  0.0961919   0.09719576  0.09493186
   0.10947946  0.09568842  0.09231497  0.11354169]
 [ 0.11963563  0.10272677  0.08718593  0.10184116  0.11153892  0.09281074
   0.09366485  0.09868772  0.08632887  0.10557938]
 [ 0.10798481  0.10546184  0.07839524  0.10862432  0.10982776  0.09561321
   0.10059962  0.09683292  0.08624057  0.11041977]
 [ 0.10588299  0.09875242  0.09887426  0.10962097  0.1133166   0.10251163
   0.09201789  0.09834777  0.08583931  0.09483615]
 [ 0.11822654  0.09784473  0.09045369  0.11219066  0.10542974  0.10096338
   0.09291764  0.09549563  0.09215075  0.09432713]
 [ 0.12295374  0.09794796  0.08250881 

INFO:tensorflow:global_step/sec: 157.136
INFO:tensorflow:probabilities = [[ 0.11899903  0.09936342  0.08645716  0.10927638  0.10652252  0.10126615
   0.1011671   0.10379703  0.08023185  0.09291933]
 [ 0.11058158  0.10430063  0.08986634  0.10236845  0.0940814   0.09763737
   0.09245638  0.10000535  0.09727679  0.11142572]
 [ 0.1241259   0.09573705  0.09330513  0.10732335  0.09835555  0.09027857
   0.08567085  0.09054162  0.10641472  0.10824722]
 [ 0.12197294  0.09624633  0.09181058  0.08918849  0.11076931  0.10132845
   0.10101212  0.08806299  0.09793274  0.10167602]
 [ 0.1128576   0.10347498  0.08371862  0.09802669  0.11047865  0.08570578
   0.1020063   0.09604859  0.09017219  0.11751062]
 [ 0.11991648  0.09677215  0.08318742  0.09955887  0.10137802  0.11837209
   0.09558577  0.09730823  0.08911867  0.09880228]
 [ 0.1101792   0.09756775  0.08519155  0.11332643  0.11502688  0.09324796
   0.09331279  0.10343713  0.07577942  0.11293094]
 [ 0.10233094  0.09108967  0.08665344  0.11226057  0

...

INFO:tensorflow:global_step/sec: 150.001
INFO:tensorflow:probabilities = [[ 0.00001966  0.0000283   0.00011283  0.00018846  0.01651656  0.00009098
   0.00000321  0.01395339  0.00016739  0.96891922]
 [ 0.0000324   0.00001437  0.00001056  0.00058494  0.00000282  0.9965468
   0.000769    0.00000015  0.00192713  0.00011194]
 [ 0.00001651  0.00000134  0.00000002  0.00000008  0.          0.99948752
   0.00031875  0.          0.00017573  0.        ]
 [ 0.00000788  0.00194519  0.00355631  0.9891209   0.00000058  0.00001826
   0.00000005  0.00508048  0.00013142  0.00013878]
 [ 0.00000016  0.          0.00000011  0.00000034  0.00001004  0.00001135
   0.00000191  0.          0.99997544  0.00000065]
 [ 0.99915588  0.00000013  0.00015974  0.00000203  0.0000001   0.00014319
   0.00010673  0.00000098  0.00000051  0.00043082]
 [ 0.          0.          0.00000001  0.00000001  0.9999696   0.00000229
   0.00000032  0.00000065  0.00000311  0.00002404]
 [ 0.00373881  0.00008278  0.00000832  0.00005129  0.

INFO:tensorflow:loss = 0.08297, step = 19901 (0.668 sec)
INFO:tensorflow:probabilities = [[ 0.00001353  0.00000158  0.00000371  0.00377736  0.00563985  0.17007938
   0.00000239  0.00232208  0.04271686  0.7754432 ]
 [ 0.00000002  0.00000005  0.00000117  0.99989128  0.          0.00010636
   0.          0.          0.00000101  0.00000002]
 [ 0.00004998  0.00016518  0.00000527  0.00010613  0.00066035  0.00412034
   0.99329114  0.          0.00159941  0.00000221]
 [ 0.00014494  0.00000745  0.0000013   0.00003052  0.00040453  0.99818534
   0.00110336  0.00000342  0.000118    0.00000107]
 [ 0.00000223  0.99972802  0.00000765  0.00007515  0.00005854  0.00000268
   0.00000642  0.00004213  0.00001959  0.00005752]
 [ 0.00000055  0.99931788  0.00001156  0.0000924   0.00001456  0.00000101
   0.00000673  0.00008637  0.00041348  0.00005546]
 [ 0.00008718  0.00028894  0.00018113  0.0010639   0.8333497   0.00376461
   0.00003758  0.00822548  0.00141102  0.15159047]
 [ 0.00002229  0.00000273  0.0000261

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.112874.
INFO:tensorflow:Starting evaluation at 2017-12-10-14:13:06
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-20000
INFO:tensorflow:Finished evaluation at 2017-12-10-14:13:07
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9698, global_step = 20000, loss = 0.100625
{'loss': 0.1006249, 'global_step': 20000, 'accuracy': 0.9698}


SystemExit: 

/opt/conda/lib/python2.7/site-packages/IPython/core/interactiveshell.py:2890: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
